## Mapping Census Tract Data using Folium
This short example uses ACS 5-year Estimates 2019 Data Profiles for census tracts in Pittsburgh, PA. The geojson used can be found [here](https://data.wprdc.org/dataset/2010-census-tracts).

![foliumgif](../Results/foliumexample.gif)

In [11]:
import pandas as pd
import geopandas as gpd
import json
import folium

#### Read in the data

In [12]:
#get the 2010 census tracts in Pittsburgh
census_json = gpd.read_file('../Data/2010_Census_Tracts/2010_Census_Tracts.geojson')

#commnuting to work category from ACS for census tracts in allegheny county
cm_df = pd.read_csv("../Data/CensusTractData/commuting_data_pa.csv") 

#### Explore data frames

In [14]:
census_json.head(1)

objectid statefp10 countyfp10 tractce10 blkgrpce10       geoid10  \
0         1        42        003    040500          1  420030405001   

      namelsad10 mtfcc10 funcstat10  aland10  ...  tractce10_1 cnt_tractce10  \
0  Block Group 1   G5030          S   268195  ...       040500             2   

  sum_lowmod2018 sum_lowmoduniv  lowmodperct  lowmodpercanno  cdbg2018  \
0           2775           2985    92.964824           92.96       Yes   

    Shape__Area Shape__Length  \
0  5.079492e+06   10442.03645   

                                            geometry  
0  POLYGON ((-79.95304 40.44203, -79.95302 40.442...  

[1 rows x 32 columns]

In [15]:
cm_df.head(1)

Unnamed: 0  tractce10  Workers_16yrs+  own_alone  carpool  public_transit  \
0           0      10300            1507        413      102             159   

   walked  other  wfh  mean_travel_time_to_work  
0     684      9  140                      15.0

#### Cleaning the ACS data

In [16]:
cm_df = cm_df.drop(columns=['Unnamed: 0'])
cm_df = cm_df.astype({'tractce10': 'str'})

for row, col in cm_df.iterrows():
    #fix census tract number
    cen_num = cm_df.loc[row]['tractce10']
    if len(cen_num) < 6:
        cen_num = '0' + cen_num
    cm_df.at[row, 'tractce10'] = cen_num
    
cm_df.head(1)

tractce10  Workers_16yrs+  own_alone  carpool  public_transit  walked  \
0    010300            1507        413      102             159     684   

   other  wfh  mean_travel_time_to_work  
0      9  140                      15.0

#### Calculate Percentage
Normally ACS comes with the percentage column but for other reasons I chose to delete it.

In [9]:
# calculate percentages - cross referenced with ACS to verify
cm_df['perc_alone'] = cm_df['own_alone'] / cm_df['Workers_16yrs+']
cm_df['perc_walk'] = cm_df['walked'] / cm_df['Workers_16yrs+']

#deal with any NaNs from divide by 0
for row, col in cm_df.iterrows():
    if pd.isna(cm_df.loc[row]['perc_alone']):
        cm_df.at[row,'perc_alone'] = 0
    if pd.isna(cm_df.loc[row]['perc_walk']):
        cm_df.at[row,'perc_walk'] = 0

#### Use Folium to visualize different census tract attributes

In [10]:
m = folium.Map(location=[40.44, -80], 
               tiles="cartodbpositron",
               zoom_start=12)

#choropleth layer for percent of commuters walking column 'perc_walk'
folium.Choropleth(
    geo_data=census_json,
    name="commute: walking",
    data=cm_df,
    columns=["tractce10", "perc_walk"],
    key_on="feature.properties.tractce10",
    fill_color="BuPu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Commuting to Work: Walking (%)",
).add_to(m)

#choropleth layer for percent of commuters driving alone column 'perc_alone'
folium.Choropleth(
    geo_data=census_json,
    name="commute: alone",
    data=cm_df,
    columns=["tractce10", "perc_alone"],
    key_on="feature.properties.tractce10",
    fill_color="BuPu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Commuting to Work: Car, Truck, Van (%)",
).add_to(m)

folium.LayerControl().add_to(m)

m